In [1]:
import pandas as pd

df = pd.read_csv('spotify_kaggle/data.csv')
df.head()

acousticness                                   artists  danceability  \
0         0.995                       ['Carl Woitschach']         0.708   
1         0.994  ['Robert Schumann', 'Vladimir Horowitz']         0.379   
2         0.604                   ['Seweryn Goszczyński']         0.749   
3         0.995                      ['Francisco Canaro']         0.781   
4         0.990  ['Frédéric Chopin', 'Vladimir Horowitz']         0.210   

   duration_ms  energy  explicit                      id  instrumentalness  \
0       158648  0.1950         0  6KbQ3uYMLKb5jDxLF7wYDD             0.563   
1       282133  0.0135         0  6KuQTIu1KoTTkLXKrwlLPV             0.901   
2       104300  0.2200         0  6L63VW0PibdM1HDSBoqnoM             0.000   
3       180760  0.1300         0  6M94FkXd15sOAOQYRnWPN8             0.887   
4       687733  0.2040         0  6N6tiFZ9vLTSOIxkj8qKrd             0.908   

   key  liveness  loudness  mode  \
0   10    0.1510   -12.428     1   
1    8    0.0763   -28.454     1   
2    5    0.1190   -19.924     0   
3    1    0.1110   -14.734     0   
4   11    0.0980   -16.829     1   

                                            name  popularity release_date  \
0                    Singende Bataillone 1. Teil           0         1928   
1       Fantasiestücke, Op. 111: Più tosto lento           0         1928   
2                 Chapter 1.18 - Zamek kaniowski           0         1928   
3  Bebamos Juntos - Instrumental (Remasterizado)           0   1928-09-25   
4    Polonaise-Fantaisie in A-Flat Major, Op. 61           1         1928   

   speechiness    tempo  valence  year  
0       0.0506  118.469   0.7790  1928  
1       0.0462   83.972   0.0767  1928  
2       0.9290  107.177   0.8800  1928  
3       0.0926  108.003   0.7200  1928  
4       0.0424   62.149   0.0693  1928

In [6]:
# No missing data, beautiful.

df.isnull().sum()

acousticness        0
artists             0
danceability        0
duration_ms         0
energy              0
explicit            0
id                  0
instrumentalness    0
key                 0
liveness            0
loudness            0
mode                0
name                0
popularity          0
release_date        0
speechiness         0
tempo               0
valence             0
year                0
dtype: int64

In [7]:
df.columns

Index(['acousticness', 'artists', 'danceability', 'duration_ms', 'energy',
       'explicit', 'id', 'instrumentalness', 'key', 'liveness', 'loudness',
       'mode', 'name', 'popularity', 'release_date', 'speechiness', 'tempo',
       'valence', 'year'],
      dtype='object')

In [8]:
# Breakdown of feature separation

features_to_drop = ['explicit',
                    'mode',
                    'name',
                    'release_date']


normalized_numeric_features = ['acousticness',
                               'danceability',
                               'energy',
                               'instrumentalness',
                               'liveness',
                               'loudness',
                               'valence',
                               'speechiness']

numeric_features_to_normalize = ['duration_ms',
                                 'tempo',
                                 'popularity']

features_to_encode = ['key',
                      'year',
                      'artists']

labels = df.columns.drop(features_to_drop)

target = 'id'

In [9]:
# Drop excess features, check work

df = df.drop(columns = features_to_drop)
len(df.columns)

15

In [14]:
# Create cleaning pipeline

!pip install category_encoders

from sklearn.pipeline import make_pipeline
import category_encoders as ce
from sklearn import preprocessing
#from google.colab import files

def pipeline(df):
    '''
    Takes our Spotify dataset from kaggle, applies categorical encoding,
    normalizes numeric data, and returns the result as a pandas df ready
    for machine learning
    '''
    # Removes brackets from our 'artists' column string values
    for x in df['artists']:
        x = x.replace('[', '')
        x = x.replace(']', '')

    normalizer = preprocessing.MinMaxScaler(feature_range=(0,1))
    encoder = ce.OrdinalEncoder()
    df_encoded = encoder.fit_transform(df)
    df_clean = normalizer.fit_transform(df_encoded)

    # We could drop the label headers from this step, as we are
    # using unsupervised techniques
    new_df = pd.DataFrame(df_clean, columns=labels)

    new_df.to_csv('spotify2.csv', index=False)
    #files.download('spotify2.csv')

    return new_df

In [15]:
# Seems right

pipeline(df)

acousticness   artists  danceability  duration_ms  energy        id  \
0           0.998996  0.000000      0.716599     0.028442  0.1950  0.000000   
1           0.997992  0.000030      0.383603     0.051316  0.0135  0.000006   
2           0.606426  0.000060      0.758097     0.018374  0.2200  0.000012   
3           0.998996  0.000090      0.790486     0.032538  0.1300  0.000018   
4           0.993976  0.000120      0.212551     0.126450  0.2040  0.000024   
...              ...       ...           ...          ...     ...       ...   
169904      0.173695  0.999910      0.885628     0.029396  0.4430  0.999976   
169905      0.016767  0.999940      0.727733     0.030076  0.3850  0.999982   
169906      0.540161  0.999970      0.520243     0.032527  0.5390  0.999988   
169907      0.071687  1.000000      0.653846     0.030046  0.7610  0.999994   
169908      0.109438  0.533499      0.518219     0.038841  0.4280  1.000000   

        instrumentalness       key  liveness  loudness  popularity  \
0               0.563000  0.909091    0.1510  0.745000        0.00   
1               0.901000  0.727273    0.0763  0.494026        0.00   
2               0.000000  0.454545    0.1190  0.627609        0.00   
3               0.887000  0.090909    0.1110  0.708887        0.00   
4               0.908000  1.000000    0.0980  0.676079        0.01   
...                  ...       ...       ...       ...         ...   
169904          0.000032  0.090909    0.0891  0.822786        0.75   
169905          0.031300  0.727273    0.1110  0.768820        0.64   
169906          0.002330  0.636364    0.1080  0.793485        0.70   
169907          0.000000  0.090909    0.2220  0.899585        0.70   
169908          0.000000  0.000000    0.1050  0.823945        0.65   

        speechiness     tempo  valence      year  
0          0.052219  0.485348   0.7790  0.070707  
1          0.047678  0.344019   0.0767  0.070707  
2          0.958720  0.439086   0.8800  0.070707  
3          0.095562  0.442470   0.7200  0.070707  
4          0.043756  0.254614   0.0693  0.070707  
...             ...       ...      ...       ...  
169904     0.147575  0.409732   0.3060  1.000000  
169905     0.041589  0.524395   0.2700  1.000000  
169906     0.108359  0.506778   0.1530  1.000000  
169907     0.039732  0.532244   0.4720  1.000000  
169908     0.027967  0.330156   0.3660  1.000000  

[169909 rows x 15 columns]

In [8]:
# Imports back in well.

new_df = pd.read_csv('spotify2.csv')
new_df.head()

acousticness  artists  danceability  duration_ms  energy        id  \
0      0.998996  0.00000      0.716599     0.028442  0.1950  0.000000   
1      0.997992  0.00003      0.383603     0.051316  0.0135  0.000006   
2      0.606426  0.00006      0.758097     0.018374  0.2200  0.000012   
3      0.998996  0.00009      0.790486     0.032538  0.1300  0.000018   
4      0.993976  0.00012      0.212551     0.126450  0.2040  0.000024   

   instrumentalness       key  liveness  loudness  popularity  speechiness  \
0             0.563  0.909091    0.1510  0.745000        0.00     0.052219   
1             0.901  0.727273    0.0763  0.494026        0.00     0.047678   
2             0.000  0.454545    0.1190  0.627609        0.00     0.958720   
3             0.887  0.090909    0.1110  0.708887        0.00     0.095562   
4             0.908  1.000000    0.0980  0.676079        0.01     0.043756   

      tempo  valence      year  
0  0.485348   0.7790  0.070707  
1  0.344019   0.0767  0.070707  
2  0.439086   0.8800  0.070707  
3  0.442470   0.7200  0.070707  
4  0.254614   0.0693  0.070707

## Visualizations

In [24]:

new_df.columns.tolist()

['acousticness',
 'artists',
 'danceability',
 'duration_ms',
 'energy',
 'id',
 'instrumentalness',
 'key',
 'liveness',
 'loudness',
 'popularity',
 'speechiness',
 'tempo',
 'valence',
 'year']

In [2]:
def heigher_order_features(input_y):
    """A helper function for compare_this function, it creates
    a list with a specific row input"""
    state = []
    for i, x in enumerate(new_df.columns.tolist()):
        a = new_df[str(x)][input_y]
        state.append(a)
        
    return state

In [3]:
print(heigher_order_features(2))

NameError: name 'new_df' is not defined

In [50]:
import plotly.graph_objects as go
import plotly.offline as pyo

def compare_this(a,b):

    categories = new_df.columns.tolist()

    fig = go.Figure()

    fig.add_trace(go.Scatterpolar(
        r=heigher_order_features(a),
        theta=categories,
        fill='toself',
        name='Product A'
    ))
    fig.add_trace(go.Scatterpolar(
        r=heigher_order_features(b),
        theta=categories,
        fill='toself',
        name='Product B'
    ))

    fig.update_layout(
    polar=dict(
      radialaxis=dict(
        visible=True,
        range=[0, 1]
      )),
    showlegend=False
    )
    
    pyo.iplot(fig, filename = 'basic-line')

compare_this(100,200)

In [53]:
new_df.values.tolist()

[[0.9989959839357432,
  0.0,
  0.7165991902834008,
  0.028441802670128438,
  0.195,
  0.0,
  0.563,
  0.9090909090909092,
  0.151,
  0.7450003915120195,
  0.0,
  0.052218782249742,
  0.4853476777103621,
  0.779,
  0.07070707070707273],
 [0.997991967871486,
  2.9963444597590942e-05,
  0.3836032388663968,
  0.0513162067519365,
  0.0135,
  5.885538055889069e-06,
  0.901,
  0.7272727272727273,
  0.0763,
  0.4940255265836662,
  0.0,
  0.04767801857585138,
  0.3440192387265406,
  0.0767,
  0.07070707070707273],
 [0.606425702811245,
  5.9926889195181884e-05,
  0.7580971659919029,
  0.01837436036508649,
  0.22,
  1.1771076111778136e-05,
  0.0,
  0.4545454545454546,
  0.119,
  0.6276094276094277,
  0.0,
  0.9587203302373579,
  0.4390862424259805,
  0.88,
  0.07070707070707273],
 [0.9989959839357432,
  8.989033379277281e-05,
  0.7904858299595141,
  0.032537837193001184,
  0.13,
  1.7656614167667205e-05,
  0.887,
  0.09090909090909093,
  0.111,
  0.7088873228408112,
  0.0,
  0.09556243550051598,


In [78]:
samples = new_df.values.tolist()
from sklearn.neighbors import NearestNeighbors
neigh = NearestNeighbors(n_neighbors=20)
neigh.fit(samples)



NearestNeighbors(n_neighbors=20)

In [79]:
def value_monad(a):
    return new_df.values.tolist()[a]

value_monad(1)

[0.997991967871486,
 2.9963444597590942e-05,
 0.3836032388663968,
 0.0513162067519365,
 0.0135,
 5.885538055889069e-06,
 0.901,
 0.7272727272727273,
 0.0763,
 0.4940255265836662,
 0.0,
 0.04767801857585138,
 0.3440192387265406,
 0.0767,
 0.07070707070707273]

In [80]:

print(neigh.kneighbors([value_monad(10000)]))

(array([[0.        , 0.26437765, 0.26623907, 0.28723417, 0.30341281,
        0.31390304, 0.32246313, 0.32313638, 0.32415728, 0.32679204,
        0.32883792, 0.33545995, 0.33711348, 0.33724571, 0.34088624,
        0.34282455, 0.34399587, 0.34404901, 0.34761091, 0.3498265 ]]), array([[10000, 18201,  2611, 35170, 26469, 26655, 18360,  8941, 49579,
         3038, 11263, 11720, 11185, 19080, 26064, 18835,  1449, 19030,
        10249, 19130]]))


In [81]:
compare_this(10000,18201)

In [88]:
df = pd.read_csv('spotify_kaggle/data.csv')

df.values[10000]

array([0.488, "['Martin Denny']", 0.301, 186000, 0.249, 0,
       '6UMAEsJEaKEN7Y2GXtid5a', 0.0012, 1, 0.11199999999999999, -16.408,
       1, 'Forbidden Island', 10, '1958-01-01', 0.0315, 89.51799999999999,
       0.0494, 1958], dtype=object)

In [89]:
df.values[18201]

array([0.54, "['Eddie Cochran']", 0.33, 139533, 0.185, 0,
       '2Bpf44xO9EcGEVewLuOLmN', 0.0288, 2, 0.122, -14.31, 1,
       'Tell Me Why', 17, '1960-05-01', 0.0343, 140.356, 0.0795, 1960],
      dtype=object)

In [91]:
neigh

NearestNeighbors(n_neighbors=20)

In [93]:
import pickle
filename = 'neighbors'
outfile = open(filename,'wb')

pickle.dump(neigh, outfile)
outfile.close()

In [5]:
import pickle
filename = 'neighbors'

infile = open(filename,'rb')
model = pickle.load(infile)
infile.close()

In [6]:
model

NearestNeighbors(n_neighbors=20)

In [10]:
print(new_dict.kneighbors([value_monad(10000)]))

NameError: name 'new_dict' is not defined

## Fuzzy string matching
https://www.datacamp.com/community/tutorials/fuzzy-string-python

But method takes forever to search :<

In [104]:
import numpy as np
def levenshtein_ratio_and_distance(s, t, ratio_calc = False):
    """ levenshtein_ratio_and_distance:
        Calculates levenshtein distance between two strings.
        If ratio_calc = True, the function computes the
        levenshtein distance ratio of similarity between two strings
        For all i and j, distance[i,j] will contain the Levenshtein
        distance between the first i characters of s and the
        first j characters of t
    """
    # Initialize matrix of zeros
    rows = len(s)+1
    cols = len(t)+1
    distance = np.zeros((rows,cols),dtype = int)

    # Populate matrix of zeros with the indeces of each character of both strings
    for i in range(1, rows):
        for k in range(1,cols):
            distance[i][0] = i
            distance[0][k] = k

    # Iterate over the matrix to compute the cost of deletions,insertions and/or substitutions    
    for col in range(1, cols):
        for row in range(1, rows):
            if s[row-1] == t[col-1]:
                cost = 0 # If the characters are the same in the two strings in a given position [i,j] then the cost is 0
            else:
                # In order to align the results with those of the Python Levenshtein package, if we choose to calculate the ratio
                # the cost of a substitution is 2. If we calculate just distance, then the cost of a substitution is 1.
                if ratio_calc == True:
                    cost = 2
                else:
                    cost = 1
            distance[row][col] = min(distance[row-1][col] + 1,      # Cost of deletions
                                 distance[row][col-1] + 1,          # Cost of insertions
                                 distance[row-1][col-1] + cost)     # Cost of substitutions
    if ratio_calc == True:
        # Computation of the Levenshtein Distance Ratio
        Ratio = ((len(s)+len(t)) - distance[row][col]) / (len(s)+len(t))
        return Ratio
    else:
        # print(distance) # Uncomment if you want to see the matrix showing how the algorithm computes the cost of deletions,
        # insertions and/or substitutions
        # This is the minimum number of edits needed to convert string a to string b
        return "The strings are {} edits away".format(distance[row][col])

In [105]:
Str1 = "Apple Inc."
Str2 = "apple Inc"
Distance = levenshtein_ratio_and_distance(Str1,Str2)
print(Distance)
Ratio = levenshtein_ratio_and_distance(Str1,Str2,ratio_calc = True)
print(Ratio)

The strings are 2 edits away
0.8421052631578947


In [149]:
df

acousticness                                   artists  danceability  \
0             0.9950                       ['Carl Woitschach']         0.708   
1             0.9940  ['Robert Schumann', 'Vladimir Horowitz']         0.379   
2             0.6040                   ['Seweryn Goszczyński']         0.749   
3             0.9950                      ['Francisco Canaro']         0.781   
4             0.9900  ['Frédéric Chopin', 'Vladimir Horowitz']         0.210   
...              ...                                       ...           ...   
169904        0.1730                    ['DripReport', 'Tyga']         0.875   
169905        0.0167        ['Leon Bridges', 'Terrace Martin']         0.719   
169906        0.5380                     ['Kygo', 'Oh Wonder']         0.514   
169907        0.0714             ['Cash Cash', 'Andy Grammer']         0.646   
169908        0.1090                        ['Ingrid Andress']         0.512   

        duration_ms  energy  explicit                      id  \
0            158648  0.1950         0  6KbQ3uYMLKb5jDxLF7wYDD   
1            282133  0.0135         0  6KuQTIu1KoTTkLXKrwlLPV   
2            104300  0.2200         0  6L63VW0PibdM1HDSBoqnoM   
3            180760  0.1300         0  6M94FkXd15sOAOQYRnWPN8   
4            687733  0.2040         0  6N6tiFZ9vLTSOIxkj8qKrd   
...             ...     ...       ...                     ...   
169904       163800  0.4430         1  4KppkflX7I3vJQk7urOJaS   
169905       167468  0.3850         0  1ehhGlTvjtHo2e4xJFB0SZ   
169906       180700  0.5390         0  52eycxprLhK3lPcRLbQiVk   
169907       167308  0.7610         0  3wYOGJYD31sLRmBgCvWxa4   
169908       214787  0.4280         0  60RFlt48hm0l4Fu0JoccOl   

        instrumentalness  key  liveness  loudness  mode  \
0               0.563000   10    0.1510   -12.428     1   
1               0.901000    8    0.0763   -28.454     1   
2               0.000000    5    0.1190   -19.924     0   
3               0.887000    1    0.1110   -14.734     0   
4               0.908000   11    0.0980   -16.829     1   
...                  ...  ...       ...       ...   ...   
169904          0.000032    1    0.0891    -7.461     1   
169905          0.031300    8    0.1110   -10.907     1   
169906          0.002330    7    0.1080    -9.332     1   
169907          0.000000    1    0.2220    -2.557     1   
169908          0.000000    0    0.1050    -7.387     1   

                                                 name  popularity  \
0                         Singende Bataillone 1. Teil           0   
1            Fantasiestücke, Op. 111: Più tosto lento           0   
2                      Chapter 1.18 - Zamek kaniowski           0   
3       Bebamos Juntos - Instrumental (Remasterizado)           0   
4         Polonaise-Fantaisie in A-Flat Major, Op. 61           1   
...                                               ...         ...   
169904                  Skechers (feat. Tyga) - Remix          75   
169905                 Sweeter (feat. Terrace Martin)          64   
169906                               How Would I Know          70   
169907                                    I Found You          70   
169908                          More Hearts Than Mine          65   

       release_date  speechiness    tempo  valence  year  
0              1928       0.0506  118.469   0.7790  1928  
1              1928       0.0462   83.972   0.0767  1928  
2              1928       0.9290  107.177   0.8800  1928  
3        1928-09-25       0.0926  108.003   0.7200  1928  
4              1928       0.0424   62.149   0.0693  1928  
...             ...          ...      ...      ...   ...  
169904   2020-05-15       0.1430  100.012   0.3060  2020  
169905   2020-06-08       0.0403  128.000   0.2700  2020  
169906   2020-05-29       0.1050  123.700   0.1530  2020  
169907   2020-02-28       0.0385  129.916   0.4720  2020  
169908   2020-03-27       0.0271   80.588   0.3660  2020  

[169909 rows x 19 c

In [137]:
df = pd.read_csv('spotify_kaggle/data.csv')
df['artists'].values.tolist()

["['Carl Woitschach']",
 "['Robert Schumann', 'Vladimir Horowitz']",
 "['Seweryn Goszczyński']",
 "['Francisco Canaro']",
 "['Frédéric Chopin', 'Vladimir Horowitz']",
 "['Felix Mendelssohn', 'Vladimir Horowitz']",
 "['Franz Liszt', 'Vladimir Horowitz']",
 "['Carl Woitschach']",
 "['Francisco Canaro', 'Charlo']",
 "['Seweryn Goszczyński']",
 "['Sergei Rachmaninoff', 'Vladimir Horowitz']",
 "['Frédéric Chopin', 'Vladimir Horowitz']",
 "['Samuel Barber', 'Vladimir Horowitz']",
 "['Robert Schumann', 'Vladimir Horowitz']",
 "['Ludwig van Beethoven', 'Staatskapelle Berlin', 'Richard Strauss']",
 "['George Butterworth', 'John Cameron']",
 "['Alexander Scriabin', 'Vladimir Horowitz']",
 "['Francisco Canaro', 'Luis Scalon']",
 "['Thomas Arne', 'John Heddle Nash']",
 "['Francisco Canaro']",
 "['Moritz Moszkowski', 'Vladimir Horowitz']",
 "['Francisco Canaro']",
 "['Frédéric Chopin', 'Vladimir Horowitz']",
 "['Francisco Canaro']",
 "['Francisco Canaro', 'Charlo']",
 "['Roger Quilter', 'John Heddl

In [145]:
def clean_string(a):
    s = df['artists'].values.tolist()[a]
    s1 = s.replace("[", "")
    s2 = s1.replace(']', '')
    s3 = s2.replace("'", "")
    return s3

In [148]:
clean_string(10)

'Sergei Rachmaninoff, Vladimir Horowitz'

In [152]:
song_list = df['name'].values.tolist()

In [155]:
Str1 = "Hey Jude"
Str2 = "hey jude"

Ratio = levenshtein_ratio_and_distance(Str1.lower(),Str2.lower(),ratio_calc = True)
Ratio

1.0

In [157]:
def string_matching(song_in):
    song_list = df['name'].values.tolist()
    
    state = []
    for index, x in enumerate(song_list):
        Ratio = levenshtein_ratio_and_distance(song_in.lower(),x.lower(),ratio_calc = True)
        state.append(Ratio)
        print(Ratio)
    return state

print(string_matching("hey_jude"))

0.17142857142857143
0.08333333333333333
0.15789473684210525
0.1509433962264151
0.0784313725490196
0.17142857142857143
0.1111111111111111
0.14814814814814814
0.15
0.16216216216216217
0.04819277108433735
0.07407407407407407
0.09523809523809523
0.10256410256410256
0.11320754716981132
0.1702127659574468
0.10126582278481013
0.09302325581395349
0.2222222222222222
0.09230769230769231
0.20512820512820512
0.09836065573770492
0.08333333333333333
0.125
0.17142857142857143
0.11428571428571428
0.0
0.1
0.03333333333333333
0.15789473684210525
0.10526315789473684
0.10810810810810811
0.2222222222222222
0.13793103448275862
0.125
0.16
0.16216216216216217
0.16
0.15789473684210525
0.15789473684210525
0.08333333333333333
0.0784313725490196
0.10256410256410256
0.13043478260869565
0.16216216216216217
0.15789473684210525
0.10344827586206896
0.05
0.13333333333333333
0.07017543859649122
0.17647058823529413
0.1875
0.11764705882352941
0.0975609756097561
0.07692307692307693
0.25806451612903225
0.16666666666666666
0

0.15
0.25
0.0
0.13636363636363635
0.20512820512820512
0.0
0.08791208791208792
0.10126582278481013
0.06451612903225806
0.0
0.0
0.14814814814814814
0.05
0.12307692307692308
0.0
0.3333333333333333
0.21621621621621623
0.13793103448275862
0.1276595744680851
0.0
0.0
0.09411764705882353
0.11764705882352941
0.21052631578947367
0.0
0.12121212121212122
0.14285714285714285
0.11764705882352941
0.15
0.18181818181818182
0.0
0.0
0.10526315789473684
0.0
0.07792207792207792
0.12903225806451613
0.0
0.10526315789473684
0.0
0.13793103448275862
0.0
0.20689655172413793
0.10810810810810811
0.0
0.0
0.07692307692307693
0.0
0.17391304347826086
0.21428571428571427
0.0
0.0
0.08333333333333333
0.15384615384615385
0.08791208791208792
0.0
0.0
0.07894736842105263
0.08823529411764706
0.11764705882352941
0.0898876404494382
0.08823529411764706
0.23076923076923078
0.17142857142857143
0.25
0.21621621621621623
0.0
0.24390243902439024
0.13513513513513514
0.2962962962962963
0.09876543209876543
0.05128205128205128
0.32
0.0
0.

0.17142857142857143
0.24
0.10909090909090909
0.1875
0.0
0.15789473684210525
0.14814814814814814
0.17142857142857143
0.375
0.15384615384615385
0.15789473684210525
0.23076923076923078
0.14035087719298245
0.1111111111111111
0.07692307692307693
0.17391304347826086
0.19047619047619047
0.2222222222222222
0.17647058823529413
0.08955223880597014
0.17391304347826086
0.13333333333333333
0.13333333333333333
0.25806451612903225
0.12903225806451613
0.07042253521126761
0.375
0.2857142857142857
0.21428571428571427
0.0
0.15625
0.0970873786407767
0.07317073170731707
0.10526315789473684
0.12121212121212122
0.0
0.058823529411764705
0.08791208791208792
0.35294117647058826
0.2608695652173913
0.25
0.125
0.13513513513513514
0.08333333333333333
0.12121212121212122
0.1951219512195122
0.38095238095238093
0.3333333333333333
0.08421052631578947
0.12903225806451613
0.2222222222222222
0.11764705882352941
0.09090909090909091
0.23529411764705882
0.06666666666666667
0.1875
0.3333333333333333
0.07894736842105263
0.1578

0.2
0.10526315789473684
0.2
0.23529411764705882
0.13333333333333333
0.21621621621621623
0.17857142857142858
0.06896551724137931
0.0
0.18181818181818182
0.16216216216216217
0.35294117647058826
0.08
0.14814814814814814
0.15384615384615385
0.0
0.3333333333333333
0.0
0.1
0.11320754716981132
0.24
0.14545454545454545
0.21621621621621623
0.29411764705882354
0.13793103448275862
0.11764705882352941
0.0
0.21428571428571427
0.24242424242424243
0.125
0.2962962962962963
0.15
0.1702127659574468
0.0
0.15384615384615385
0.21052631578947367
0.16
0.08421052631578947
0.23529411764705882
0.3076923076923077
0.21052631578947367
0.13333333333333333
0.12987012987012986
0.14285714285714285
0.13333333333333333
0.2727272727272727
0.14814814814814814
0.11764705882352941
0.14814814814814814
0.12244897959183673
0.12121212121212122
0.25
0.27586206896551724
0.12307692307692308
0.10810810810810811
0.13333333333333333
0.25806451612903225
0.1875
0.34782608695652173
0.23529411764705882
0.15789473684210525
0.2424242424242

0.08888888888888889
0.17543859649122806
0.08
0.18181818181818182
0.17647058823529413
0.15789473684210525
0.10810810810810811
0.10666666666666667
0.0625
0.26666666666666666
0.16216216216216217
0.18181818181818182
0.1095890410958904
0.15873015873015872
0.12903225806451613
0.3
0.13793103448275862
0.09302325581395349
0.09302325581395349
0.14814814814814814
0.375
0.11764705882352941
0.2222222222222222
0.25
0.2222222222222222
0.21428571428571427
0.06666666666666667
0.12121212121212122
0.15384615384615385
0.16666666666666666
0.14705882352941177
0.15384615384615385
0.16666666666666666
0.26666666666666666
0.09523809523809523
0.24242424242424243
0.10526315789473684
0.08695652173913043
0.19047619047619047
0.17142857142857143
0.3333333333333333
0.19047619047619047
0.17647058823529413
0.35714285714285715
0.12903225806451613
0.0963855421686747
0.2
0.09523809523809523
0.15384615384615385
0.18181818181818182
0.12903225806451613
0.25
0.21052631578947367
0.1875
0.2
0.2
0.15384615384615385
0.156862745098

...

0.0
0.15384615384615385
0.24
0.1388888888888889
0.12903225806451613
0.0273972602739726
0.14285714285714285
0.0898876404494382
0.0
0.1111111111111111
0.17777777777777778
0.15789473684210525
0.17391304347826086
0.09523809523809523
0.11428571428571428
0.10344827586206896
0.18181818181818182
0.2
0.08
0.13793103448275862
0.2608695652173913
0.06451612903225806
0.11428571428571428
0.15
0.1
0.08
0.0
0.22857142857142856
0.0
0.11267605633802817
0.18181818181818182
0.18604651162790697
0.03508771929824561
0.22857142857142856
0.06451612903225806
0.09090909090909091
0.14814814814814814
0.16666666666666666
0.0
0.11940298507462686
0.11764705882352941
0.0
0.0
0.0851063829787234
0.0
0.15384615384615385
0.15384615384615385
0.16
0.21428571428571427
0.24
0.0
0.1875
0.2857142857142857
0.08955223880597014
0.08333333333333333
0.09523809523809523
0.1
0.18867924528301888
0.25
0.14634146341463414
0.06382978723404255
0.13043478260869565
0.08
0.1276595744680851
0.08
0.07894736842105263
0.09375
0.1951219512195122
0

0.13793103448275862
0.32
0.13793103448275862
0.2222222222222222
0.0967741935483871
0.2222222222222222
0.13333333333333333
0.125
0.15384615384615385
0.1875
0.18181818181818182
0.18181818181818182
0.17857142857142858
0.1
0.2
0.09090909090909091
0.0
0.1
0.3333333333333333
0.1111111111111111
0.21621621621621623
0.2608695652173913
0.25
0.16666666666666666
0.3157894736842105
0.20689655172413793
0.09302325581395349
0.12903225806451613
0.13333333333333333
0.375
0.058823529411764705
0.13333333333333333
0.16
0.11267605633802817
0.13043478260869565
0.2
0.07692307692307693
0.0821917808219178
0.09523809523809523
0.19607843137254902
0.21428571428571427
0.1935483870967742
0.0
0.22857142857142856
0.3076923076923077
0.16666666666666666
0.4
0.17647058823529413
0.10101010101010101
0.26666666666666666
0.1
0.10666666666666667
0.21428571428571427
0.12121212121212122
0.18181818181818182
0.21428571428571427
0.06629834254143646
0.25806451612903225
0.0975609756097561
0.15384615384615385
0.2727272727272727
0.095

0.16326530612244897
0.2
0.26666666666666666
0.35294117647058826
0.11764705882352941
0.15384615384615385
0.24242424242424243
0.17647058823529413
0.2
0.25
0.14814814814814814
0.16216216216216217
0.2222222222222222
0.0
0.13513513513513514
0.14285714285714285
0.02857142857142857
0.15384615384615385
0.125
0.2
0.11428571428571428
0.10526315789473684
0.2
0.1935483870967742
0.08108108108108109
0.12903225806451613
0.0
0.17142857142857143
0.10256410256410256
0.12903225806451613
0.2222222222222222
0.2608695652173913
0.2857142857142857
0.18181818181818182
0.2857142857142857
0.2222222222222222
0.2
0.16666666666666666
0.25
0.11428571428571428
0.11594202898550725
0.14814814814814814
0.35294117647058826
0.17391304347826086
0.23529411764705882
0.2
0.0784313725490196
0.2608695652173913
0.13333333333333333
0.1702127659574468
0.11764705882352941
0.08333333333333333
0.2
0.12698412698412698
0.23076923076923078
0.1935483870967742
0.12987012987012986
0.13513513513513514
0.09523809523809523
0.24
0.133333333333

0.0
0.0
0.0
0.11764705882352941
0.125
0.17142857142857143
0.2222222222222222
0.2857142857142857
0.3225806451612903
0.0
0.16666666666666666
0.1111111111111111
0.14285714285714285
0.16666666666666666
0.14285714285714285
0.22857142857142856
0.45454545454545453
0.17142857142857143
0.23529411764705882
0.0
0.14285714285714285
0.26666666666666666
0.15384615384615385
0.25806451612903225
0.2608695652173913
0.125
0.16
0.15384615384615385
0.16666666666666666
0.4
0.1875
0.23076923076923078
0.11904761904761904
0.26666666666666666
0.14545454545454545
0.17391304347826086
0.19047619047619047
0.23529411764705882
0.1935483870967742
0.20689655172413793
0.2608695652173913
0.2608695652173913
0.14285714285714285
0.2
0.05747126436781609
0.22857142857142856
0.20512820512820512
0.21621621621621623
0.17142857142857143
0.1694915254237288
0.24242424242424243
0.2
0.125
0.23076923076923078
0.1568627450980392
0.14285714285714285
0.18604651162790697
0.15384615384615385
0.14814814814814814
0.14285714285714285
0.059880

KeyboardInterrupt: 

## 

In [158]:
song_list

['Singende Bataillone 1. Teil',
 'Fantasiestücke, Op. 111: Più tosto lento',
 'Chapter 1.18 - Zamek kaniowski',
 'Bebamos Juntos - Instrumental (Remasterizado)',
 'Polonaise-Fantaisie in A-Flat Major, Op. 61',
 'Scherzo a capriccio: Presto',
 'Valse oubliée No. 1 in F-Sharp Major, S. 215/1',
 'Per aspera ad astra',
 'Moneda Corriente - Remasterizado',
 'Chapter 1.3 - Zamek kaniowski',
 'Piano Sonata No. 2 in B-Flat Minor, Op. 36: I. Allegro agitato - Meno mosso',
 'Piano Sonata No. 2, Op. 35: IV. Finale. Presto',
 'Piano Sonata in E-Flat Minor, Op. 26: III. Adagio mesto',
 'Nachtstücke, Op. 23: No. 4 in F',
 'Symphony No. 5 in C Minor, Op. 67: 3. Allegro',
 'A Shropshire Lad: Is My Team Ploughing?',
 'Sonata No. 3, Op. 23 in F-Sharp Minor: IV. Presto con fuoco; Meno mosso',
 'Invocación al Tango - Remasterizado',
 'Where the Bee Sucks',
 'Tendrás Que Llorar Conmigo - Instrumental (Remasterizado)',
 'Etude in A-Flat, Op. 72, No. 11',
 'Quisiste Cachar un Gil - Instrumental (Remasterizad

In [ ]:
[{
    name: ''
}]

In [170]:
state = []
for i, x in enumerate(song_list):
    state.append({'name': x})

In [182]:
state

[{'name': 'Singende Bataillone 1. Teil'},
 {'name': 'Fantasiestücke, Op. 111: Più tosto lento'},
 {'name': 'Chapter 1.18 - Zamek kaniowski'},
 {'name': 'Bebamos Juntos - Instrumental (Remasterizado)'},
 {'name': 'Polonaise-Fantaisie in A-Flat Major, Op. 61'},
 {'name': 'Scherzo a capriccio: Presto'},
 {'name': 'Valse oubliée No. 1 in F-Sharp Major, S. 215/1'},
 {'name': 'Per aspera ad astra'},
 {'name': 'Moneda Corriente - Remasterizado'},
 {'name': 'Chapter 1.3 - Zamek kaniowski'},
 {'name': 'Piano Sonata No. 2 in B-Flat Minor, Op. 36: I. Allegro agitato - Meno mosso'},
 {'name': 'Piano Sonata No. 2, Op. 35: IV. Finale. Presto'},
 {'name': 'Piano Sonata in E-Flat Minor, Op. 26: III. Adagio mesto'},
 {'name': 'Nachtstücke, Op. 23: No. 4 in F'},
 {'name': 'Symphony No. 5 in C Minor, Op. 67: 3. Allegro'},
 {'name': 'A Shropshire Lad: Is My Team Ploughing?'},
 {'name': 'Sonata No. 3, Op. 23 in F-Sharp Minor: IV. Presto con fuoco; Meno mosso'},
 {'name': 'Invocación al Tango - Remasterizad

In [185]:
translation = {39: None} 
# formatting dict list
test = str(state).translate(translation)

In [186]:
test

'[{name: Singende Bataillone 1. Teil}, {name: Fantasiestücke, Op. 111: Più tosto lento}, {name: Chapter 1.18 - Zamek kaniowski}, {name: Bebamos Juntos - Instrumental (Remasterizado)}, {name: Polonaise-Fantaisie in A-Flat Major, Op. 61}, {name: Scherzo a capriccio: Presto}, {name: Valse oubliée No. 1 in F-Sharp Major, S. 215/1}, {name: Per aspera ad astra}, {name: Moneda Corriente - Remasterizado}, {name: Chapter 1.3 - Zamek kaniowski}, {name: Piano Sonata No. 2 in B-Flat Minor, Op. 36: I. Allegro agitato - Meno mosso}, {name: Piano Sonata No. 2, Op. 35: IV. Finale. Presto}, {name: Piano Sonata in E-Flat Minor, Op. 26: III. Adagio mesto}, {name: Nachtstücke, Op. 23: No. 4 in F}, {name: Symphony No. 5 in C Minor, Op. 67: 3. Allegro}, {name: A Shropshire Lad: Is My Team Ploughing?}, {name: Sonata No. 3, Op. 23 in F-Sharp Minor: IV. Presto con fuoco; Meno mosso}, {name: Invocación al Tango - Remasterizado}, {name: Where the Bee Sucks}, {name: Tendrás Que Llorar Conmigo - Instrumental (Rema

In [187]:
with open('song_list.json', 'w') as f:
    f.write(str(test))